In [1]:
link1 = 'http://people.brunel.ac.uk/~mastjjb/jeb/orlib/files/cap82.txt'
link2 = 'http://people.brunel.ac.uk/~mastjjb/jeb/orlib/files/cap113.txt'
import numpy as np
import gurobipy as gp
from gurobipy import GRB

In [2]:
# define function to download data
def load_data(url, filename):
    import urllib.request
    response = urllib.request.urlretrieve(url,filename)
    file = open(filename,'r')
    return file

In [3]:
#solution encode: facility opening decision: 0 = close, 1 = open for each location
#for example: starting solution could be open all facilities
#decision = np.ones(locations)

#for a given location-opening decision, there is an optimized location-customer allocation
#allocation = np.zeros(varcost.shape)

In [4]:
#define a function to allocate transportation with a given decision
def allocate(capacity, demand, fixcost, varcost, decision):
    import numpy as np
    import gurobipy as gp
    from gurobipy import GRB
    
    model = gp.Model("Fixed-Charge Transportation problem")

    (locations,customers) = varcost.shape
    
    # Create variables
    transport = {} # transport quantity

    for n in range(locations):
        for m in range(customers):
            transport[n,m] = model.addVar(obj=varcost[n][m])

    # supply constraints
    for n in range(locations):
        model.addConstr(sum(transport[n,m] for m in range(customers)) <= capacity[n])

    # Demand constraints
    for m in range(customers):
        model.addConstr(sum(transport[n,m] for n in range(locations)) >= demand[m])

    # Binding constraints
    for n in range(locations):
        for m in range(customers):
            model.addConstr(transport[n,m] <= decision[n] * min(capacity[n], demand[m]))

    model.optimize()

    solution = np.zeros(varcost.shape)
    for i in range(n):
        for j in range(m):
            solution[n,m] = transport[n,m].x

    cost = model.objVal

    model.dispose()
    return (cost, solution)



In [5]:
# check feasibility of a decision
def feasible(capacity, demand, decision):
    if np.dot(capacity, decision) >= sum(demand):
        return True
    else:
        return False

In [6]:
# repair a decision by random open new locations
def repair(capacity, demand, decision):
    sum_cap = np.dot(capacity, decision)
    sum_demand = sum(demand)
    decision_idx = [list(x) for x in enumerate(decision)]
    
    while sum_cap < sum_demand: #loop until get enough capacity to fulfill demand
        random_idx = np.random.choice([d[0] for d in decision_idx if d[1] == 0])
        decision_idx[random_idx][1] = 1
        sum_cap += capacity[decision_idx[random_idx][0]]
        
    new_decision = [d[1] for d in decision_idx]
    
    return new_decision

In [7]:
#format of a solution
def create_solution(capacity, demand, fixcost, varcost, decision):
    (vc, allocation) = allocate(capacity, demand, fixcost, varcost, decision)
    solution = [vc + np.dot(fixcost, decision), decision, allocation]
    
    return solution

In [8]:
# random initialize
def initialize(capacity, demand, fixcost, varcost, pop_size, infeasible = 'repair'):
    solution_pop = []
    decision_pop = []
    
    penalty = False
    penalty_cost = 100*(np.max(fixcost)*len(capacity) + np.max(varcost)*len(capacity)*len(demand)) #big cost
    
    while len(decision_pop) < pop_size: #iterate to get pop_size candidates 
        decision = list(np.random.choice([0,1], size = len(capacity)))
        
        if not feasible(capacity, demand, decision):
            if infeasible == 'reject':
                continue #continue loop without add decision
            elif infeasible == 'penalty':
                penalty = True
            else: #repair
                decision = repair(capacity, demand, decision)

        if decision not in decision_pop:
            decision_pop.append(decision)
            if penalty:
                solution_pop.append([penalty_cost, decision, None])
            else: solution_pop.append(create_solution(capacity, demand, fixcost, varcost, decision))
    
    return solution_pop #return a population of solution candidates

In [9]:
# use Fitnessproportional selection (roulette wheel selection)
def select_fitness(solution_pop, offspring_size):
    
    expected = np.mean([ sol[0] for sol in solution_pop])
    
    pop_size = len(solution_pop)
    f = [ (2*expected - solution_pop[i][0]) for i in range(pop_size)] #calculate f of each candidate
    sum_f = sum(f)
    prob_range = [ sum(f[0:i+1])/sum_f for i in range(pop_size)] #cumulative prob of each candidate
    
    offspring = []
    for i in range(offspring_size):
        p = np.random.random()
        for j in range(pop_size):
            if prob_range[j] >= p:
                offspring.append(solution_pop[j])
                break
    
    return offspring

In [10]:
#recombination and mutation
# use Uniform crossover
def recomb_uniform(capacity, demand, fixcost, varcost, solution_pop, offspring,
                   recprob, muprob, crossprob = 0.5, mulocprob = 0.5, infeasible = "repair"):
    locations = len(offspring[0][1])
    penalty_cost = 100*(np.max(fixcost)*len(capacity) + np.max(varcost)*len(capacity)*len(demand)) #big cost
    
    pop = [s[1] for s in solution_pop] #set of decision
    
    for k in range(len(offspring)//2): 
        penalty = False

        #recombination
        if np.random.random() < recprob:
            child = []
            #uniform crossover
            for i in range(locations):
                if np.random.random() < crossprob:
                    child.append(offspring[2*k][1][i]) #from offspring1
                else: 
                    child.append(offspring[2*k+1][1][i]) #from offspring2
    
            #mutation
            if np.random.random() < muprob:
                for i in range(locations):
                    if np.random.random() < mulocprob:
                        child[i] = abs(child[i] - 1)


            #infeasible solution
            if not feasible(capacity, demand, child):
                if infeasible == "reject":
                    continue #continue loop without add decision
                elif infeasible == "penalty":
                    penalty = True
                else: #repair
                    child = repair(capacity, demand, child)
        

            if child not in pop:
                pop.append(child)
                if penalty:
                    solution_pop.append([penalty_cost, child, None])
                else: solution_pop.append(create_solution(capacity, demand, fixcost, varcost, child))
            
    return solution_pop

In [11]:
# replacement
# use Deterministic (N,M): best N out of N+M
def replace_best(solution_pop, pop_size):
    sortedpop = sorted(solution_pop) #sorted by cost of a solution
    pop = sortedpop[0:pop_size]
    
    return pop 

In [12]:
file = load_data(link2, 'cap113.txt')
data = file.readlines()

In [13]:
[locations, customers] = [int(x) for x in data[0].split(' ')[1:-1]]
capacity = []
fixcost = []
for i in range(locations):
    [c, f] = [float(x) for x in data[i+1].split(' ')[1:-1]]
    capacity.append(c)
    fixcost.append(f)
demand = []
varcost = np.zeros((locations,customers))
for j in range(customers):
    demand.append(float(data[j*9 + (1+locations)].split(' ')[1]))
    v = list(np.concatenate([data[j*9 + (1+locations+t)].split(' ')[1:-1] for t in range(1,9)]))
    for i in range(locations):
        varcost[i,j] = float(v[i])/demand[j] #cost of allocating demand of j to warehouse i per unit
        
        
print(locations)
print(customers)
print(capacity)
print(fixcost)
print(demand)
print(varcost)


50
50
[5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0]
[17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 0.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0]
[146.0, 87.0, 672.0, 1337.0, 31.0, 559.0, 2370.0, 1089.0, 33.0, 32.0, 5495.0, 904.0, 1466.0, 143.0, 615.0, 564.0, 226.0, 3016.0, 253.0, 195.0, 38.

In [14]:
#parameters
pop_size = 100
offspring_size = 500
iterations = 50
recombination = 0.7
crossover = 0.5
mutation = 0.3
location_mutation = 0.3

In [15]:
#main algorithm    
solution_pop = initialize(capacity, demand, fixcost, varcost, pop_size)

for it in range(iterations):
    offspring = select_fitness(solution_pop, offspring_size)
    solution_pop = recomb_uniform(capacity, demand, fixcost, varcost, solution_pop, offspring, infeasible = 'repair', 
                       recprob = recombination, muprob = mutation, crossprob = crossover, mulocprob = location_mutation)
    solution_pop = replace_best(solution_pop, pop_size)
    


Using license file C:\Users\hadao\gurobi.lic
Academic license - for non-commercial use only
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0x09d23ab1
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 2523 rows and 1150 columns
Presolve time: 0.01s
Presolved: 77 rows, 1350 columns, 2700 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      65    8.0738018e+05   0.000000e+00   0.000000e+00      0s

Solved in 65 iterations and 0.02 seconds
Optimal objective  8.073801750e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0xe457c2e7
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objecti

      63    7.5291976e+05   0.000000e+00   0.000000e+00      0s

Solved in 63 iterations and 0.01 seconds
Optimal objective  7.529197625e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0xb52df84b
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 2521 rows and 1050 columns
Presolve time: 0.01s
Presolved: 79 rows, 1450 columns, 2900 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      61    8.0161516e+05   0.000000e+00   0.000000e+00      0s

Solved in 61 iterations and 0.01 seconds
Optimal objective  8.016151625e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0xf7f99885
Coefficient statis

       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      57    7.4718173e+05   0.000000e+00   0.000000e+00      0s

Solved in 57 iterations and 0.01 seconds
Optimal objective  7.471817250e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0x1098076f
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 2525 rows and 1250 columns
Presolve time: 0.01s
Presolved: 75 rows, 1250 columns, 2500 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      63    8.4616308e+05   0.000000e+00   0.000000e+00      0s

Solved in 63 iterations and 0.02 seconds
Optimal objective  8.461630750e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns an


Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      57    7.3052316e+05   0.000000e+00   0.000000e+00      0s

Solved in 57 iterations and 0.01 seconds
Optimal objective  7.305231625e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0x1cfb5cd7
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 2525 rows and 1250 columns
Presolve time: 0.01s
Presolved: 75 rows, 1250 columns, 2500 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      78    1.0588354e+06   0.000000e+00   0.000000e+00      0s

Solved in 78 iterations and 0.01 seconds
Optimal objective  1.058835350e+06
Gurobi Optimizer version 9.0.2 build v

Presolve time: 0.01s
Presolved: 72 rows, 1100 columns, 2200 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      66    8.6204441e+05   0.000000e+00   0.000000e+00      0s

Solved in 66 iterations and 0.01 seconds
Optimal objective  8.620444125e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0x2c25bd1d
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 2523 rows and 1150 columns
Presolve time: 0.01s
Presolved: 77 rows, 1350 columns, 2700 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      66    8.6390739e+05   0.000000e+00   0.000000e+00      0s

Solved in 66 iterations and 0.01 seconds
Opti

...

       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      83    9.7838474e+05   0.000000e+00   0.000000e+00      0s

Solved in 83 iterations and 0.00 seconds
Optimal objective  9.783847375e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0x024b99bc
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 2536 rows and 1800 columns
Presolve time: 0.01s
Presolved: 64 rows, 700 columns, 1400 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      59    7.5990165e+05   0.000000e+00   0.000000e+00      0s

Solved in 59 iterations and 0.01 seconds
Optimal objective  7.599016500e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and


Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      54    7.6424349e+05   0.000000e+00   0.000000e+00      0s

Solved in 54 iterations and 0.02 seconds
Optimal objective  7.642434875e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0x80dfc799
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 2535 rows and 1750 columns
Presolve time: 0.00s
Presolved: 65 rows, 750 columns, 1500 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      54    7.3678872e+05   0.000000e+00   0.000000e+00      0s

Solved in 54 iterations and 0.00 seconds
Optimal objective  7.367887250e+05
Gurobi Optimizer version 9.0.2 build v9

Presolve time: 0.02s
Presolved: 67 rows, 850 columns, 1700 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      53    7.1719266e+05   0.000000e+00   0.000000e+00      0s

Solved in 53 iterations and 0.02 seconds
Optimal objective  7.171926625e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0xc6231e2c
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 2531 rows and 1550 columns
Presolve time: 0.00s
Presolved: 69 rows, 950 columns, 1900 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      63    7.8079167e+05   0.000000e+00   0.000000e+00      0s

Solved in 63 iterations and 0.02 seconds
Optima

  RHS range        [3e+01, 1e+04]
Presolve removed 2525 rows and 1250 columns
Presolve time: 0.00s
Presolved: 75 rows, 1250 columns, 2500 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      58    7.1482641e+05   0.000000e+00   0.000000e+00      0s

Solved in 58 iterations and 0.01 seconds
Optimal objective  7.148264125e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0xf22fc5b9
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 2534 rows and 1700 columns
Presolve time: 0.02s
Presolved: 66 rows, 800 columns, 1600 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      56    7.3699548e+05   0.000

  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 2536 rows and 1800 columns
Presolve time: 0.00s
Presolved: 64 rows, 700 columns, 1400 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      69    7.8083015e+05   0.000000e+00   0.000000e+00      0s

Solved in 69 iterations and 0.00 seconds
Optimal objective  7.808301500e+05
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 2600 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0x633e650b
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 2534 rows and 1700 columns
Presolve time: 0.02s
Presolved: 66 rows, 800 columns, 1600 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      T

In [17]:
best_solution = solution_pop[0]
print('Best objective value', best_solution[0])
print('Decision', best_solution[1])

Best objective value 970567.7499999999
Decision [0, 0, 0, 1, 0, 1, 1, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1, 0]
